In [1]:
# Copyright 2015 The TensorFlow Authors. All Rights Reserved.
#
# Licensed under the Apache License, Version 2.0 (the 'License');
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
#     http://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an 'AS IS' BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.
# ==============================================================================
"""A simple MNIST classifier which displays summaries in TensorBoard.

This is an unimpressive MNIST model, but it is a good example of using
tf.name_scope to make a graph legible in the TensorBoard graph explorer, and of
naming summary tags so that they are grouped meaningfully in TensorBoard.

It demonstrates the functionality of every TensorBoard dashboard.
"""
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import argparse
import os
import sys

import tensorflow as tf

from tensorflow.examples.tutorials.mnist import input_data

FLAGS = None


def train():
  # Import data
  mnist = input_data.read_data_sets(FLAGS.data_dir,
                                    fake_data=FLAGS.fake_data)

  sess = tf.InteractiveSession()
  # Create a multilayer model.

  # Input placeholders
  with tf.name_scope('input'):
    x = tf.placeholder(tf.float32, [None, 784], name='x-input')
    y_ = tf.placeholder(tf.int64, [None], name='y-input')

  with tf.name_scope('input_reshape'):
    image_shaped_input = tf.reshape(x, [-1, 28, 28, 1])
    tf.summary.image('input', image_shaped_input, 10)

  # We can't initialize these variables to 0 - the network will get stuck.
  def weight_variable(shape):
    """Create a weight variable with appropriate initialization."""
    initial = tf.truncated_normal(shape, stddev=0.1)
    return tf.Variable(initial)

  def bias_variable(shape):
    """Create a bias variable with appropriate initialization."""
    initial = tf.constant(0.1, shape=shape)
    return tf.Variable(initial)

  def variable_summaries(var):
    """Attach a lot of summaries to a Tensor (for TensorBoard visualization)."""
    with tf.name_scope('summaries'):
      mean = tf.reduce_mean(var)
      tf.summary.scalar('mean', mean)
      with tf.name_scope('stddev'):
        stddev = tf.sqrt(tf.reduce_mean(tf.square(var - mean)))
      tf.summary.scalar('stddev', stddev)
      tf.summary.scalar('max', tf.reduce_max(var))
      tf.summary.scalar('min', tf.reduce_min(var))
      tf.summary.histogram('histogram', var)

  def nn_layer(input_tensor, input_dim, output_dim, layer_name, act=tf.nn.relu):
    """Reusable code for making a simple neural net layer.

    It does a matrix multiply, bias add, and then uses ReLU to nonlinearize.
    It also sets up name scoping so that the resultant graph is easy to read,
    and adds a number of summary ops.
    """
    # Adding a name scope ensures logical grouping of the layers in the graph.
    with tf.name_scope(layer_name):
      # This Variable will hold the state of the weights for the layer
      with tf.name_scope('weights'):
        weights = weight_variable([input_dim, output_dim])
        variable_summaries(weights)
      with tf.name_scope('biases'):
        biases = bias_variable([output_dim])
        variable_summaries(biases)
      with tf.name_scope('Wx_plus_b'):
        preactivate = tf.matmul(input_tensor, weights) + biases
        tf.summary.histogram('pre_activations', preactivate)
      activations = act(preactivate, name='activation')
      tf.summary.histogram('activations', activations)
      return activations

  hidden1 = nn_layer(x, 784, 500, 'layer1')

  with tf.name_scope('dropout'):
    keep_prob = tf.placeholder(tf.float32)
    tf.summary.scalar('dropout_keep_probability', keep_prob)
    dropped = tf.nn.dropout(hidden1, keep_prob)

  # Do not apply softmax activation yet, see below.
  y = nn_layer(dropped, 500, 10, 'layer2', act=tf.identity)

  with tf.name_scope('cross_entropy'):
    # The raw formulation of cross-entropy,
    #
    # tf.reduce_mean(-tf.reduce_sum(y_ * tf.log(tf.softmax(y)),
    #                               reduction_indices=[1]))
    #
    # can be numerically unstable.
    #
    # So here we use tf.losses.sparse_softmax_cross_entropy on the
    # raw logit outputs of the nn_layer above, and then average across
    # the batch.
    with tf.name_scope('total'):
      cross_entropy = tf.losses.sparse_softmax_cross_entropy(
          labels=y_, logits=y)
  tf.summary.scalar('cross_entropy', cross_entropy)

  with tf.name_scope('train'):
    train_step = tf.train.AdamOptimizer(FLAGS.learning_rate).minimize(
        cross_entropy)

  with tf.name_scope('accuracy'):
    with tf.name_scope('correct_prediction'):
      correct_prediction = tf.equal(tf.argmax(y, 1), y_)
    with tf.name_scope('accuracy'):
      accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))
  tf.summary.scalar('accuracy', accuracy)

  # Merge all the summaries and write them out to
  # /tmp/tensorflow/mnist/logs/mnist_with_summaries (by default)
  merged = tf.summary.merge_all()
  train_writer = tf.summary.FileWriter(FLAGS.log_dir + '/train', sess.graph)
  test_writer = tf.summary.FileWriter(FLAGS.log_dir + '/test')
  tf.global_variables_initializer().run()

  # Train the model, and also write summaries.
  # Every 10th step, measure test-set accuracy, and write test summaries
  # All other steps, run train_step on training data, & add training summaries

  def feed_dict(train):
    """Make a TensorFlow feed_dict: maps data onto Tensor placeholders."""
    if train or FLAGS.fake_data:
      xs, ys = mnist.train.next_batch(100, fake_data=FLAGS.fake_data)
      k = FLAGS.dropout
    else:
      xs, ys = mnist.test.images, mnist.test.labels
      k = 1.0
    return {x: xs, y_: ys, keep_prob: k}

  for i in range(FLAGS.max_steps):
    if i % 10 == 0:  # Record summaries and test-set accuracy
      summary, acc = sess.run([merged, accuracy], feed_dict=feed_dict(False))
      test_writer.add_summary(summary, i)
      print('Accuracy at step %s: %s' % (i, acc))
    else:  # Record train set summaries, and train
      if i % 100 == 99:  # Record execution stats
        run_options = tf.RunOptions(trace_level=tf.RunOptions.FULL_TRACE)
        run_metadata = tf.RunMetadata()
        summary, _ = sess.run([merged, train_step],
                              feed_dict=feed_dict(True),
                              options=run_options,
                              run_metadata=run_metadata)
        train_writer.add_run_metadata(run_metadata, 'step%03d' % i)
        train_writer.add_summary(summary, i)
        print('Adding run metadata for', i)
      else:  # Record a summary
        summary, _ = sess.run([merged, train_step], feed_dict=feed_dict(True))
        train_writer.add_summary(summary, i)
  train_writer.close()
  test_writer.close()


def main(_):
  if tf.gfile.Exists(FLAGS.log_dir):
    tf.gfile.DeleteRecursively(FLAGS.log_dir)
  tf.gfile.MakeDirs(FLAGS.log_dir)
  with tf.Graph().as_default():
    train()


if __name__ == '__main__':
  parser = argparse.ArgumentParser()
  parser.add_argument('--fake_data', nargs='?', const=True, type=bool,
                      default=False,
                      help='If true, uses fake data for unit testing.')
  parser.add_argument('--max_steps', type=int, default=1000,
                      help='Number of steps to run trainer.')
  parser.add_argument('--learning_rate', type=float, default=0.001,
                      help='Initial learning rate')
  parser.add_argument('--dropout', type=float, default=0.9,
                      help='Keep probability for training dropout.')
  parser.add_argument(
      '--data_dir',
      type=str,
      default=os.path.join(os.getenv('TEST_TMPDIR', '/tmp'),
                           'tensorflow/mnist/input_data'),
      help='Directory for storing input data')
  parser.add_argument(
      '--log_dir',
      type=str,
      default=os.path.join(os.getenv('TEST_TMPDIR', '/tmp'),
                           'tensorflow/mnist/logs/mnist_with_summaries'),
      help='Summaries log directory')
  FLAGS, unparsed = parser.parse_known_args()
  tf.app.run(main=main, argv=[sys.argv[0]] + unparsed)

Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting /tmp\tensorflow/mnist/input_data\train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting /tmp\tensorflow/mnist/input_data\train-labels-idx1-ubyte.gz
Extracting /tmp\tensorflow/mnist/input_data\t10k-images-idx3-ubyte.gz
Extracting /tmp\tensorflow/mnist/input_data\t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Accuracy at step 0: 0.1004 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5

Accuracy at step 10: 0.7188 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5\x1d\xec\x92\xf7\x14\x18\x18\x18>_\x85\n>\xe9:\xc3\xc0\xc0\xc0\xc0\xc0\x02\xe1\xa6\xea_\xd32t\xb0x,\xcb\xc0\xf0\xe7\xb5$\xc3\xa33\xc8:\x19\x18\x18\x18\x18\x04\r\xcf\x9820\xfc\xb8u](g\x1a.g\x04\xff\xbd(\x84KN\xec\xe5\xff`(\x93\tC2[\xf4\xfdM\\\x1a\xad\x7f\xfe\xb3\xc3%\xc7\xd0\xfao7+.9\xce\xb3?\xacpj\xac\xfb\xb7\r\xa7\x9c\xf7\xef\x0f\x96\xb8\xe4\x84\xef\xfe[\x86K\x8e\xf9\xf4\xbf\xdb\xca\xb8$\xd5\xfe\xfd\xf3\xc5%\'\xff\xe0_1#.\xc9\xd6\x7f\xffLp\xc9\xd9~B\x97D\n[\x1b\x1e\x86\xbb_P$Y\x909\x17\x9d\xdf\xe12\x16\x13\x00\x00i\x11<\x90\x8e\t\xbc\xff\x00\x00\x00\x00IEND\xaeB`\x82\n\xd1\x02\n\x1binput_reshape/input/image/1"\xb1\x02\x08\x1c\x10\x1c\x18\x01"\xa8\x02\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1

Accuracy at step 20: 0.8153 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5\x1d\xec\x92\xf7\x14\x18\x18\x18>_\x85\n>\xe9:\xc3\xc0\xc0\xc0\xc0\xc0\x02\xe1\xa6\xea_\xd32t\xb0x,\xcb\xc0\xf0\xe7\xb5$\xc3\xa33\xc8:\x19\x18\x18\x18\x18\x04\r\xcf\x9820\xfc\xb8u](g\x1a.g\x04\xff\xbd(\x84KN\xec\xe5\xff`(\x93\tC2[\xf4\xfdM\\\x1a\xad\x7f\xfe\xb3\xc3%\xc7\xd0\xfao7+.9\xce\xb3?\xacpj\xac\xfb\xb7\r\xa7\x9c\xf7\xef\x0f\x96\xb8\xe4\x84\xef\xfe[\x86K\x8e\xf9\xf4\xbf\xdb\xca\xb8$\xd5\xfe\xfd\xf3\xc5%\'\xff\xe0_1#.\xc9\xd6\x7f\xffLp\xc9\xd9~B\x97D\n[\x1b\x1e\x86\xbb_P$Y\x909\x17\x9d\xdf\xe12\x16\x13\x00\x00i\x11<\x90\x8e\t\xbc\xff\x00\x00\x00\x00IEND\xaeB`\x82\n\xd1\x02\n\x1binput_reshape/input/image/1"\xb1\x02\x08\x1c\x10\x1c\x18\x01"\xa8\x02\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1

Accuracy at step 30: 0.8496 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5\x1d\xec\x92\xf7\x14\x18\x18\x18>_\x85\n>\xe9:\xc3\xc0\xc0\xc0\xc0\xc0\x02\xe1\xa6\xea_\xd32t\xb0x,\xcb\xc0\xf0\xe7\xb5$\xc3\xa33\xc8:\x19\x18\x18\x18\x18\x04\r\xcf\x9820\xfc\xb8u](g\x1a.g\x04\xff\xbd(\x84KN\xec\xe5\xff`(\x93\tC2[\xf4\xfdM\\\x1a\xad\x7f\xfe\xb3\xc3%\xc7\xd0\xfao7+.9\xce\xb3?\xacpj\xac\xfb\xb7\r\xa7\x9c\xf7\xef\x0f\x96\xb8\xe4\x84\xef\xfe[\x86K\x8e\xf9\xf4\xbf\xdb\xca\xb8$\xd5\xfe\xfd\xf3\xc5%\'\xff\xe0_1#.\xc9\xd6\x7f\xffLp\xc9\xd9~B\x97D\n[\x1b\x1e\x86\xbb_P$Y\x909\x17\x9d\xdf\xe12\x16\x13\x00\x00i\x11<\x90\x8e\t\xbc\xff\x00\x00\x00\x00IEND\xaeB`\x82\n\xd1\x02\n\x1binput_reshape/input/image/1"\xb1\x02\x08\x1c\x10\x1c\x18\x01"\xa8\x02\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1

Accuracy at step 40: 0.8749 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5\x1d\xec\x92\xf7\x14\x18\x18\x18>_\x85\n>\xe9:\xc3\xc0\xc0\xc0\xc0\xc0\x02\xe1\xa6\xea_\xd32t\xb0x,\xcb\xc0\xf0\xe7\xb5$\xc3\xa33\xc8:\x19\x18\x18\x18\x18\x04\r\xcf\x9820\xfc\xb8u](g\x1a.g\x04\xff\xbd(\x84KN\xec\xe5\xff`(\x93\tC2[\xf4\xfdM\\\x1a\xad\x7f\xfe\xb3\xc3%\xc7\xd0\xfao7+.9\xce\xb3?\xacpj\xac\xfb\xb7\r\xa7\x9c\xf7\xef\x0f\x96\xb8\xe4\x84\xef\xfe[\x86K\x8e\xf9\xf4\xbf\xdb\xca\xb8$\xd5\xfe\xfd\xf3\xc5%\'\xff\xe0_1#.\xc9\xd6\x7f\xffLp\xc9\xd9~B\x97D\n[\x1b\x1e\x86\xbb_P$Y\x909\x17\x9d\xdf\xe12\x16\x13\x00\x00i\x11<\x90\x8e\t\xbc\xff\x00\x00\x00\x00IEND\xaeB`\x82\n\xd1\x02\n\x1binput_reshape/input/image/1"\xb1\x02\x08\x1c\x10\x1c\x18\x01"\xa8\x02\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1

...

Accuracy at step 970: 0.9679 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5\x1d\xec\x92\xf7\x14\x18\x18\x18>_\x85\n>\xe9:\xc3\xc0\xc0\xc0\xc0\xc0\x02\xe1\xa6\xea_\xd32t\xb0x,\xcb\xc0\xf0\xe7\xb5$\xc3\xa33\xc8:\x19\x18\x18\x18\x18\x04\r\xcf\x9820\xfc\xb8u](g\x1a.g\x04\xff\xbd(\x84KN\xec\xe5\xff`(\x93\tC2[\xf4\xfdM\\\x1a\xad\x7f\xfe\xb3\xc3%\xc7\xd0\xfao7+.9\xce\xb3?\xacpj\xac\xfb\xb7\r\xa7\x9c\xf7\xef\x0f\x96\xb8\xe4\x84\xef\xfe[\x86K\x8e\xf9\xf4\xbf\xdb\xca\xb8$\xd5\xfe\xfd\xf3\xc5%\'\xff\xe0_1#.\xc9\xd6\x7f\xffLp\xc9\xd9~B\x97D\n[\x1b\x1e\x86\xbb_P$Y\x909\x17\x9d\xdf\xe12\x16\x13\x00\x00i\x11<\x90\x8e\t\xbc\xff\x00\x00\x00\x00IEND\xaeB`\x82\n\xd1\x02\n\x1binput_reshape/input/image/1"\xb1\x02\x08\x1c\x10\x1c\x18\x01"\xa8\x02\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x

Accuracy at step 980: 0.967 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5\x1d\xec\x92\xf7\x14\x18\x18\x18>_\x85\n>\xe9:\xc3\xc0\xc0\xc0\xc0\xc0\x02\xe1\xa6\xea_\xd32t\xb0x,\xcb\xc0\xf0\xe7\xb5$\xc3\xa33\xc8:\x19\x18\x18\x18\x18\x04\r\xcf\x9820\xfc\xb8u](g\x1a.g\x04\xff\xbd(\x84KN\xec\xe5\xff`(\x93\tC2[\xf4\xfdM\\\x1a\xad\x7f\xfe\xb3\xc3%\xc7\xd0\xfao7+.9\xce\xb3?\xacpj\xac\xfb\xb7\r\xa7\x9c\xf7\xef\x0f\x96\xb8\xe4\x84\xef\xfe[\x86K\x8e\xf9\xf4\xbf\xdb\xca\xb8$\xd5\xfe\xfd\xf3\xc5%\'\xff\xe0_1#.\xc9\xd6\x7f\xffLp\xc9\xd9~B\x97D\n[\x1b\x1e\x86\xbb_P$Y\x909\x17\x9d\xdf\xe12\x16\x13\x00\x00i\x11<\x90\x8e\t\xbc\xff\x00\x00\x00\x00IEND\xaeB`\x82\n\xd1\x02\n\x1binput_reshape/input/image/1"\xb1\x02\x08\x1c\x10\x1c\x18\x01"\xa8\x02\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1

Accuracy at step 990: 0.968 b'\n\xa7\x02\n\x1binput_reshape/input/image/0"\x87\x02\x08\x1c\x10\x1c\x18\x01"\xfe\x01\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1c\x08\x00\x00\x00\x00Wf\x80H\x00\x00\x00\xc5IDAT(\x91c`\x186\x80\x11B\x85\xa4>\xfb\xb1\xf4\xc5\x1d\xec\x92\xf7\x14\x18\x18\x18>_\x85\n>\xe9:\xc3\xc0\xc0\xc0\xc0\xc0\x02\xe1\xa6\xea_\xd32t\xb0x,\xcb\xc0\xf0\xe7\xb5$\xc3\xa33\xc8:\x19\x18\x18\x18\x18\x04\r\xcf\x9820\xfc\xb8u](g\x1a.g\x04\xff\xbd(\x84KN\xec\xe5\xff`(\x93\tC2[\xf4\xfdM\\\x1a\xad\x7f\xfe\xb3\xc3%\xc7\xd0\xfao7+.9\xce\xb3?\xacpj\xac\xfb\xb7\r\xa7\x9c\xf7\xef\x0f\x96\xb8\xe4\x84\xef\xfe[\x86K\x8e\xf9\xf4\xbf\xdb\xca\xb8$\xd5\xfe\xfd\xf3\xc5%\'\xff\xe0_1#.\xc9\xd6\x7f\xffLp\xc9\xd9~B\x97D\n[\x1b\x1e\x86\xbb_P$Y\x909\x17\x9d\xdf\xe12\x16\x13\x00\x00i\x11<\x90\x8e\t\xbc\xff\x00\x00\x00\x00IEND\xaeB`\x82\n\xd1\x02\n\x1binput_reshape/input/image/1"\xb1\x02\x08\x1c\x10\x1c\x18\x01"\xa8\x02\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x00\x1c\x00\x00\x00\x1

SystemExit: 

C:\Users\tglkwon\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3273: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [3]:
tensorboard --logdir=/tmp/tensorflow/mnist

SyntaxError: can't assign to operator (<ipython-input-3-00b49b51d432>, line 1)